In [1]:
from pathlib import Path
import sys
from pathlib import Path
current_dir = Path().resolve()
sys.path.append(current_dir.parent.parent.as_posix())

data_dir = Path(r'D:\ACJ\20260120 Test PV chip')
print(data_dir.is_dir())
recname = r'retina2_9000mV_1s_on_5s_off_880nm_3rdq_20n006.raw'

recfile = data_dir / recname
print(recfile.is_file())

True
True


In [2]:
import numpy as np
from pv_chip_aarhus.preprocessing.params import (data_sample_rate, data_type, data_nb_channels,
                                         data_trigger_channels, data_voltage_resolution,
                                         data_trigger_thresholds)
import utils

data = np.memmap(recfile.as_posix(), dtype=data_type, mode='r')
n_samples = int(data.size / data_nb_channels)
rec_duration = (n_samples / data_sample_rate) / 60  # [min]

print(f'\treading data ({rec_duration:.0f} min)')

	reading data (3 min)


In [3]:
stimtype = 'laser_880'
trigger_channel = data_trigger_channels[stimtype]
print(f'stimtype: {stimtype}, trigger channel: {trigger_channel}')
channel_data = data[trigger_channel::data_nb_channels]
# Convert data to voltage
channel_data = channel_data.astype(float)
channel_data = channel_data - np.iinfo('uint16').min + np.iinfo('int16').min
channel_data = channel_data * data_voltage_resolution

print(np.min(channel_data), np.max(channel_data))


stimtype: laser_880, trigger channel: 127
17.75 4064.0


In [4]:

tdur = 10
t0 = 80
t1 = t0 + tdur
i0 = int(t0 * data_sample_rate)
i1 = int(t1 * data_sample_rate)

y = channel_data[i0:i1]
x = np.linspace(t0, t1, y.size)


fig = utils.make_figure(
    width=1, height=1, 
    x_domains={1: [[0.1, 0.9]]},
    y_domains={1: [[0.1, 0.9]]}
)
fig.add_scatter(x=x, y=y, mode='lines', line=dict(color='black', width=0.1))
fig.show()

